In [1]:
from datasets import Audio, interleave_datasets, IterableDataset, IterableDatasetDict, load_dataset
from transformers import WhisperProcessor
from transformers.models.whisper.english_normalizer import BasicTextNormalizer
from typing import List, Optional

/home/ubuntu/hf_env/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
def load_multiple_streaming_datasets(
    dataset_names: List,
    dataset_config_names: List,
    splits: Optional[List] = None,
    text_column_names: Optional[List] = None,
    sampling_rate: Optional[int] = 16000,
    stopping_strategy: Optional[str] = "all_exhausted",
    **kwargs
) -> IterableDataset:

    if len(dataset_names) != len(dataset_config_names):
        raise ValueError(
            f"Ensure one config is passed for each dataset, got {len(dataset_names)} datasets and"
            f" {len(dataset_config_names)} configs."
        )

    if splits is not None and len(splits) != len(dataset_names):
        raise ValueError(
            f"Ensure one split is passed for each dataset, got {len(dataset_names)} datasets and {len(splits)} splits."
        )

    if text_column_names is not None and len(text_column_names) != len(dataset_names):
        raise ValueError(
            f"Ensure one text column name is passed for each dataset, got {len(dataset_names)} datasets and"
            f" {len(text_column_names)} text column names."
        )

    splits = splits if splits is not None else ["train" for i in range(len(dataset_names))]
    text_column_names = (
        text_column_names if text_column_names is not None else ["text" for i in range(len(dataset_names))]
    )

    all_datasets = []
    # iterate over the datasets we want to interleave
    for i, dataset_name in enumerate(dataset_names):
        dataset = load_dataset(dataset_name, dataset_config_names[i], split=splits[i], streaming=True, **kwargs)
        # resample to specified sampling rate
        dataset = dataset.cast_column("audio", Audio(sampling_rate))
        #  normalise columns to ["audio", "sentence"]
        if text_column_names[i] != "sentence":
            dataset = dataset.rename_column(text_column_names[i], "sentence")
        dataset = dataset.remove_columns(set(dataset.features.keys()) - set(["audio", "sentence"]))
        all_datasets.append(dataset)

    interleaved_dataset = interleave_datasets(all_datasets, stopping_strategy=stopping_strategy)
    return interleaved_dataset

In [3]:
dataset_names = ["mozilla-foundation/common_voice_11_0", "google/fleurs", "openslr", "collectivat/tv3_parla", "projecte-aina/parlament_parla", "projecte-aina/parlament_parla"]
dataset_config_names = ["ca", "ca_es", "SLR69", "ca", "clean", "other"]
text_column_names = ["sentence", "transcription", "sentence", "text", "sentence", "sentence"]

In [4]:
trainset = load_multiple_streaming_datasets(dataset_names, dataset_config_names=dataset_config_names, text_column_names=text_column_names, use_auth_token=True)

Using custom data configuration ca


In [5]:
testset = IterableDataset
testset = load_dataset("mozilla-foundation/common_voice_11_0", "ca", split="test", streaming=True, use_auth_token=True)
testset = testset.cast_column("audio", Audio(sampling_rate=16000))

In [6]:
COLUMNS_TO_KEEP = ["sentence", "audio"]
all_columns = testset.features
columns_to_remove = set(all_columns) - set(COLUMNS_TO_KEEP)

testset = testset.remove_columns(columns_to_remove)

In [7]:
trainset.features

{'audio': Audio(sampling_rate=16000, mono=True, decode=True, id=None),
 'sentence': Value(dtype='string', id=None)}

In [8]:
testset.features

{'audio': Audio(sampling_rate=16000, mono=True, decode=True, id=None),
 'sentence': Value(dtype='string', id=None)}

In [9]:
do_lower_case = True
do_remove_punctuation = True

normalizer = BasicTextNormalizer()

In [11]:
processor = WhisperProcessor.from_pretrained("openai/whisper-tiny", language="Catalan", task="transcribe")

Downloading: 100%|██████████| 185k/185k [00:00<00:00, 38.7MB/s]
Downloading: 100%|██████████| 828/828 [00:00<00:00, 1.21MB/s]
Downloading: 100%|██████████| 1.04M/1.04M [00:00<00:00, 61.5MB/s]
Downloading: 100%|██████████| 494k/494k [00:00<00:00, 51.6MB/s]
Downloading: 100%|██████████| 52.7k/52.7k [00:00<00:00, 26.2MB/s]
Downloading: 100%|██████████| 2.11k/2.11k [00:00<00:00, 4.13MB/s]
Downloading: 100%|██████████| 2.06k/2.06k [00:00<00:00, 3.02MB/s]


In [12]:
def prepare_dataset(batch):
    # load and (possibly) resample audio data to 16kHz
    audio = batch["audio"]

    # compute log-Mel input features from input audio array 
    batch["input_features"] = processor.feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]
    # compute input length of audio sample in seconds
    batch["input_length"] = len(audio["array"]) / audio["sampling_rate"]
    
    # optional pre-processing steps
    transcription = batch["sentence"]
    if do_lower_case:
        transcription = transcription.lower()
    if do_remove_punctuation:
        transcription = normalizer(transcription).strip()
    
    # encode target text to label ids
    batch["labels"] = processor.tokenizer(transcription).input_ids
    return batch

In [13]:
vectorized_trainset = trainset.map(prepare_dataset).with_format("torch")
vectorized_testset = testset.map(prepare_dataset).with_format("torch")

In [14]:
vectorized_trainset = vectorized_trainset.shuffle(  buffer_size=500,seed=0,)
vectorized_testset = vectorized_testset.shuffle(  buffer_size=500,seed=0,)

In [15]:
MAX_DURATION_IN_SECONDS = 30.0

def is_audio_length_in_range(input_length):
    return input_length < MAX_DURATION_IN_SECONDS

In [16]:
vectorized_trainset = vectorized_trainset.filter(is_audio_length_in_range, input_columns=["input_length"])
vectorized_testset = vectorized_testset.filter(is_audio_length_in_range, input_columns=["input_length"])

In [17]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch

In [18]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor)

In [19]:
import evaluate

metric = evaluate.load("wer")

In [20]:
# evaluate with the 'normalised' WER
do_normalize_eval = True

def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = processor.tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = processor.tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = processor.tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    if do_normalize_eval:
        pred_str = [normalizer(pred) for pred in pred_str]
        label_str = [normalizer(label) for label in label_str]

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}

In [21]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-tiny")

Downloading: 100%|██████████| 1.96k/1.96k [00:00<00:00, 2.74MB/s]
Downloading: 100%|██████████| 151M/151M [00:01<00:00, 90.8MB/s] 


In [22]:
model.config.forced_decoder_ids = None
model.config.suppress_tokens = []
model.config.use_cache = False

In [27]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="./whisper-tiny-ca/",
    per_device_train_batch_size=32,
    gradient_accumulation_steps=2,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-5,
    warmup_steps=100,
    max_steps=1000,
    gradient_checkpointing=True,
    fp16=True,
    evaluation_strategy="steps",
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=1000,
    eval_steps=1000,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=False,
)

PyTorch: setting up devices


In [28]:
from transformers import TrainerCallback
from transformers.trainer_pt_utils import IterableDatasetShard
from torch.utils.data import IterableDataset

# trainer callback to reinitialise and reshuffle the streamable datasets at the beginning of each epoch
class ShuffleCallback(TrainerCallback):
    def on_epoch_begin(self, args, state, control, train_dataloader, **kwargs):
        if isinstance(train_dataloader.dataset, IterableDatasetShard):
            pass  # set_epoch() is handled by the Trainer
        elif isinstance(train_dataloader.dataset, IterableDataset):
            train_dataloader.dataset.set_epoch(train_dataloader.dataset._epoch + 1)

In [29]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=vectorized_trainset,
    eval_dataset=vectorized_testset,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor,
    callbacks=[ShuffleCallback()],
)

max_steps is given, it will override any value given in num_train_epochs
Using cuda_amp half precision backend


In [30]:
model.save_pretrained(training_args.output_dir)
processor.save_pretrained(training_args.output_dir)

Configuration saved in ./whisper-tiny-ca/config.json
Model weights saved in ./whisper-tiny-ca/pytorch_model.bin
Feature extractor saved in ./whisper-tiny-ca/preprocessor_config.json
tokenizer config file saved in ./whisper-tiny-ca/tokenizer_config.json
Special tokens file saved in ./whisper-tiny-ca/special_tokens_map.json
added tokens file saved in ./whisper-tiny-ca/added_tokens.json


In [31]:
trainer.train()

/home/ubuntu/hf_env/lib/python3.8/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 64000
  Num Epochs = 9223372036854775807
  Instantaneous batch size per device = 32
  Total train batch size (w. parallel, distributed & accumulation) = 64
  Gradient Accumulation steps = 2
  Total optimization steps = 1000
  Number of trainable parameters = 37760640
Reading metadata...: 905243it [00:16, 56138.00it/s]
The following columns in the training set don't have a corresponding argument in `WhisperForConditionalGeneration.forward` and have been ignored: sentence, input_length, audio. If sentence, input_length, audio are not expected by `WhisperForConditionalGeneration.forward`,  you can safely ignore this message.


***** Running Evaluation *****
  Num examples: Unknown
  Batch size = 8
Reading metadata...: 16340it [00:00, 37574.71it/s]
The following columns in the evaluation set don't have a corresponding argument in `WhisperForConditionalGeneration.forward` and have been ignored: sentence, input_length, audio. If sentence, input_length, audio are not expected by `WhisperForConditionalGeneration.forward`,  you can safely ignore this message.
Generate config GenerationConfig {
  "begin_suppress_tokens": [
    220,
    50257
  ],
  "bos_token_id": 50257,
  "decoder_start_token_id": 50258,
  "eos_token_id": 50257,
  "max_length": 448,
  "pad_token_id": 50257,
  "suppress_tokens": [],
  "transformers_version": "4.26.0.dev0",
  "use_cache": false
}

/home/ubuntu/hf_env/lib/python3.8/site-packages/transformers/generation/utils.py:1134: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in

TrainOutput(global_step=1000, training_loss=0.7776702079772949, metrics={'train_runtime': 32524.3885, 'train_samples_per_second': 1.968, 'train_steps_per_second': 0.031, 'total_flos': 1.57560864768e+18, 'train_loss': 0.7776702079772949, 'epoch': 1.0})

In [32]:
kwargs = {
    "dataset_tags": "mozilla-foundation/common_voice_11_0",
    "dataset": "Common Voice 11.0", 
    "language": "es",
    "model_name": "Whisper Tiny Cat",
    "finetuned_from": "openai/whisper-tiny",
    "tasks": "automatic-speech-recognition",
    "tags": "whisper-event",
}

In [ ]:
trainer.push_to_hub(**kwargs)